In [5]:
import sys
import os
import torch
import torch.nn as nn
import matplotlib.pyplot as plt

rootdir = os.path.abspath(sys.path[0] + '/../')
sys.path.append(rootdir)

torch.cuda.set_device(0)
print("Set CUDA:%d as current device." % torch.cuda.current_device())
torch.autograd.set_grad_enabled(False)

from data.spherical_view_syn import *
from configs.spherical_view_syn import SphericalViewSynConfig
from utils import netio
from utils import img
from utils import device
from utils.view import *
from components.fnr import FoveatedNeuralRenderer


def load_net(path):
    config = SphericalViewSynConfig()
    config.from_id(os.path.splitext(path)[0])
    config.SAMPLE_PARAMS['perturb_sample'] = False
    net = config.create_net().to(device.default())
    netio.load(path, net)
    return net


def find_file(prefix):
    for path in os.listdir():
        if path.startswith(prefix):
            return path
    return None


def load_views(data_desc_file) -> Trans:
    with open(data_desc_file, 'r', encoding='utf-8') as file:
        data_desc = json.loads(file.read())
        view_centers = torch.tensor(
            data_desc['view_centers'], device=device.default()).view(-1, 3)
        view_rots = torch.tensor(
            data_desc['view_rots'], device=device.default()).view(-1, 3, 3)
        return Trans(view_centers, view_rots)


def plot_cross(center, res):
    plt.plot(
        [
            (res[1] - 1) / 2 + center[0] - 5,
            (res[1] - 1) / 2 + center[0] + 5
        ],
        [
            (res[0] - 1) / 2 + center[1],
            (res[0] - 1) / 2 + center[1]
        ],
        color=[0, 1, 0])
    plt.plot(
        [
            (res[1] - 1) / 2 + center[0],
            (res[1] - 1) / 2 + center[0]
        ],
        [
            (res[0] - 1) / 2 + center[1] - 5,
            (res[0] - 1) / 2 + center[1] + 5
        ],
        color=[0, 1, 0])


def plot_figures(left_images, right_images, left_center, right_center):
    # Plot Fovea
    plt.figure(figsize=(12, 6))
    plt.subplot(121)
    img.plot(left_images['layers_img'][0])
    fovea_res = left_images['layers_img'][0].size()[-2:]
    plot_cross((0, 0), fovea_res)
    plt.subplot(122)
    img.plot(right_images['layers_img'][0])
    plot_cross((0, 0), fovea_res)

    # Plot Mid
    plt.figure(figsize=(12, 6))
    plt.subplot(121)
    img.plot(left_images['layers_img'][1])
    plt.subplot(122)
    img.plot(right_images['layers_img'][1])

    # Plot Periph
    plt.figure(figsize=(12, 6))
    plt.subplot(121)
    img.plot(left_images['layers_img'][2])
    plt.subplot(122)
    img.plot(right_images['layers_img'][2])

    # Plot Blended
    plt.figure(figsize=(12, 6))
    plt.subplot(121)
    img.plot(left_images['blended'])
    full_res = left_images['blended'].size()[-2:]
    plot_cross(left_center, full_res)
    plt.subplot(122)
    img.plot(right_images['blended'])
    plot_cross(right_center, full_res)


scenes = {
    'classroom': 'classroom_all',
    'stones': 'stones_all',
    'barbershop': 'barbershop_all',
    'lobby': 'lobby_all'
}


fov_list = [20, 45, 110]
res_list = [(256, 256), (256, 256), (256, 230)]
res_full = (1600, 1440)


Set CUDA:0 as current device.


In [26]:
params = {
    'classroom': [
        [(0, 0, 0, 0, 0), (1, -83), (-5, -83)],
        [(0, 0, 0, 0, 0), (-171, 55), (-178, 55)],
        [(0, 0, 0, 0, 0), (60, 55), (55, 55)],
        [(0, 0, 0, 0, 0), (138, 160), (130, 160)]
    ],
}
scene = 'classroom'
os.chdir(f'{rootdir}/data/__new/{scenes[scene]}')
print('Change working directory to ', os.getcwd())

fovea_net = load_net(find_file('fovea'))
periph_net = load_net(find_file('periph'))
renderer = FoveatedNeuralRenderer(fov_list, res_list,
                                  nn.ModuleList([fovea_net, periph_net, periph_net]),
                                  res_full, device=device.default())

for i, param in enumerate(params[scene]):
    view = Trans(torch.tensor(param[0][:3], device=device.default()),
                 torch.tensor(euler_to_matrix([-param[0][4], param[0][3], 0]),
                              device=device.default()).view(3, 3))
    eye_offset = torch.tensor([0.03, 0, 0], device=device.default())
    left_view = Trans(view.trans_point(-eye_offset), view.r)
    right_view = Trans(view.trans_point(eye_offset), view.r)
    left_images, right_images = renderer(view, param[1], param[2],
                                         stereo_disparity=0.06, using_mask=False, ret_raw=False)
    if True:
        outputdir = '../__demo/stereo/'
        misc.create_dir(outputdir)
        img.save(left_images['blended'], '%s%s_%d_l.png' % (outputdir, scene, i))
        img.save(right_images['blended'], '%s%s_%d_r.png' % (outputdir, scene, i))
        stereo_overlap = torch.cat([
            left_images['blended'][:, 0:1],
            right_images['blended'][:, 1:3]
        ], dim=1)
        img.save(stereo_overlap, '%s%s_%d_stereo.png' % (outputdir, scene, i))
    else:
        plot_figures(left_images, right_images, param[1], param[2])


Change working directory to  /home/dengnc/dvs/data/__new/classroom_all
Load net from fovea@snerffast4-rgb_e6_fc256x8_d1.00-7.00_s64_~p.pth ...
Load net from periph@snerffast4-rgb_e6_fc128x4_d1.00-7.00_s64_~p.pth ...
